In [1]:
!pip install datasets evaluate transformers[sentencepiece]

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 468.7/468.7 kB 7.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 81.4/81.4 kB 3.7 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 7.0/7.0 MB 54.2 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 110.5/110.5 kB 1.4 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.0/1.0 MB 25.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 212.2/212.2 kB 11.3 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 200.1/200.1 kB 13.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 132.9/132.9 kB 7.9 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 7.8/7.8 MB 27.4 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.3/1.3 MB 21.1 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.0/1.0 MB 18.4 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━

Авторизация Hugging face с помощью токена

In [2]:
from huggingface_hub import notebook_login

notebook_login()

Token is valid.
Your token has been saved in your configured git credential helpers (store).
Your token has been saved to /root/.cache/huggingface/token
Login successful


In [3]:
from transformers import pipeline

Загрузка модели из Hugging face

In [4]:
model_checkpoint2 = "Stacy123/rubert_tiny_qa_kontur"
question_answerer = pipeline("question-answering", model=model_checkpoint2)

Загрузка и обработка тестовых данных

In [56]:
import json
with open('test.json', 'r') as f:
    data = json.load(f)

In [57]:
def prep_data(dataset):
  ids = []
  questions = []
  contexts = []
  for i in range(len(dataset)):
    ids.append(dataset[i]['id'])
    questions.append(dataset[i]['label'])
    contexts.append(dataset[i]['text'])
  return {
      'id': ids,
      'question': questions,
      'context': contexts,
  }

In [58]:
dataset = prep_data(data)

In [59]:
import pandas as pd

In [60]:
cols = ['id', 'context','question','answers']

data_df = pd.DataFrame(dataset, columns=cols) 

In [61]:
data_df.head()

id                                            context  \
0  762883279  МУНИЦИПАЛЬНЫЙ КОНТРАКТ № ______ на оказание ус...   
1  311837655  Извещение о проведении электронного аукциона д...   
2  540954893  Идентификационный код закупки: 222633005300163...   
3  274660397  Идентификационный код закупки: 222631202689463...   
4  732742591  Идентификационный код закупки: 222637800031163...   

                           question answers  
0  обеспечение исполнения контракта     NaN  
1  обеспечение исполнения контракта     NaN  
2  обеспечение исполнения контракта     NaN  
3  обеспечение исполнения контракта     NaN  
4  обеспечение исполнения контракта     NaN

In [62]:
len(data_df)

318

Проверка одного примера

In [63]:
data_df.iloc[0].question

'обеспечение исполнения контракта'

In [64]:
context = data_df.iloc[0].context
question = data_df.iloc[0].question
question_answerer(question=question, context=context)

{'score': 0.0013592320028692484,
 'start': 1283,
 'end': 1348,
 'answer': 'Размер обеспечения исполнения Контракта составляет _______ рублей'}

Поиск ответов по всему датафрейму

In [65]:
for i in range(len(data_df)):
  answer = question_answerer(question=data_df['question'][i], context=data_df['context'][i])
  del answer['score']
  data_df['answers'][i] = answer

<ipython-input-65-736bf97f7e74>:4: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  data_df['answers'][i] = answer


In [66]:
data_df.head()

id                                            context  \
0  762883279  МУНИЦИПАЛЬНЫЙ КОНТРАКТ № ______ на оказание ус...   
1  311837655  Извещение о проведении электронного аукциона д...   
2  540954893  Идентификационный код закупки: 222633005300163...   
3  274660397  Идентификационный код закупки: 222631202689463...   
4  732742591  Идентификационный код закупки: 222637800031163...   

                           question  \
0  обеспечение исполнения контракта   
1  обеспечение исполнения контракта   
2  обеспечение исполнения контракта   
3  обеспечение исполнения контракта   
4  обеспечение исполнения контракта   

                                             answers  
0  {'start': 1283, 'end': 1348, 'answer': 'Размер...  
1  {'start': 1291, 'end': 1337, 'answer': 'Размер...  
2   {'start': 1300, 'end': 1306, 'answer': 'Размер'}  
3  {'start': 2149, 'end': 2180, 'answer': 'по кот...  
4   {'start': 1314, 'end': 1320, 'answer': 'Размер'}

In [67]:
data_df = data_df.rename(columns={"context": "text", "question": "label", "answers": "extracted_part"})

In [68]:
for i in range(len(data_df)):
  data_df["extracted_part"][i]["text"] = [data_df["extracted_part"][i].pop("answer")]
  data_df["extracted_part"][i]["answer_start"] = [data_df["extracted_part"][i].pop("start")]
  data_df["extracted_part"][i]["answer_end"] = [data_df["extracted_part"][i].pop("end")]

In [69]:
data_df.head()

id                                               text  \
0  762883279  МУНИЦИПАЛЬНЫЙ КОНТРАКТ № ______ на оказание ус...   
1  311837655  Извещение о проведении электронного аукциона д...   
2  540954893  Идентификационный код закупки: 222633005300163...   
3  274660397  Идентификационный код закупки: 222631202689463...   
4  732742591  Идентификационный код закупки: 222637800031163...   

                              label  \
0  обеспечение исполнения контракта   
1  обеспечение исполнения контракта   
2  обеспечение исполнения контракта   
3  обеспечение исполнения контракта   
4  обеспечение исполнения контракта   

                                      extracted_part  
0  {'text': ['Размер обеспечения исполнения Контр...  
1  {'text': ['Размер обеспечения исполнения контр...  
2  {'text': ['Размер'], 'answer_start': [1300], '...  
3  {'text': ['по которой заключается контракт'], ...  
4  {'text': ['Размер'], 'answer_start': [1314], '...

Загрузка в JSON

In [70]:
data_dict = data_df.to_dict('records')

In [71]:
data_dict[0]

{'id': 762883279,
 'text': 'МУНИЦИПАЛЬНЫЙ КОНТРАКТ № ______ на оказание услуг по техническому обслуживанию и ремонту принтеров и многофункциональных устройств, заправке и восстановлению картриджей (идентификационный код закупки 223861800296886010100100590019511244) г. Ханты-Мансийск «___» ____________ 2022 г.  (или) возмещения убытков причинённых Исполнителем убытков. 6. Обеспечение исполнения контракта 6.1. Исполнение контракта обеспечиваются предоставлением независимой гарантии, выданной банком и соответствующей требованиям Федерального закона от 05.04.2013 № 44-ФЗ «О контрактной системе в сфере закупок товаров, работ, услуг для обеспечения государственных и муниципальных нужд», или внесением денежных средств на указанный заказчиком счет, на котором в соответствии с законодательством Российской Федерации учитываются операции со средствами, поступающими заказчику. Способ обеспечения исполнения контракта, срок действия независимой гарантии определяются в соответствии с требованиями Фед

In [72]:
with open('predictions.json', 'w') as f:
    json.dump(data_dict, f, ensure_ascii=False, indent=2)